In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import warnings
warnings.filterwarnings("ignore")

In [2]:
# Data source: https://www.propublica.org/datastore/dataset/chicago-parking-ticket-data
# Original csv was 7.67 GB, which is too big for my desktop to handle, 
# here I randomly choose 20% of the original dataset to analyze.

df_CCPT = pd.read_csv('./data/parking_tickets_frac.csv')

In [3]:
# Drop columns that are not needed here
col2drop = ['Unnamed: 0','ticket_number','license_plate_number','zipcode',
          'unit','unit_description','notice_number','violation_location','violation_code']
df_CCPT.drop(labels=col2drop ,axis = 1,inplace = True)

In [4]:
# Drop columns that are not needed here
row2drop= ['license_plate_state']
df_CCPT.dropna(axis = 0, how = 'any', subset = row2drop, inplace = True)

In [6]:
df_CCPT['issue_date'] = pd.to_datetime(df_CCPT['issue_date'])
# Here I choose the data between year 2016 and 2017 as a demonstration for the plot
mask1617 = ((df_CCPT['issue_date'] >= pd.Timestamp(2016,1,1,0)) & (df_CCPT['issue_date'] <pd.Timestamp(2018,1,1,0)))
df_CCPT1617 = df_CCPT.loc[mask1617]

In [7]:
# Take a look at the address column here, try to convert it to lat,long for mapping the ticket
df_CCPT1617['address'].head()

10              500 e 46, chicago, il
13     6100 s archer ave, chicago, il
20    4200 w irving park, chicago, il
25          1700 w grand, chicago, il
42       2200 n st louis, chicago, il
Name: address, dtype: object

Seems that all the address follows the same format, here split them by address, city and state

In [8]:
address_df = pd.DataFrame(df_CCPT1617['address'].str.split(', ').tolist(), columns=['address','city','state','None'])
address_df['city'].value_counts()

chicago    889767
louis           1
Name: city, dtype: int64

In [10]:
mask = (address_df['city'] == 'louis')
address_df.loc[mask]
# found only one anomoly here, there's an additional comma in the address

address   city    state None
137135  600 n st  louis  chicago   il

In [11]:
mask_add = (df_CCPT1617['address'] == '600 n st, louis, chicago, il')
# Change it to correct form
df_CCPT1617['address'] = df_CCPT1617['address'].str.replace('600 n st, louis, chicago, il','600 n st louis, chicago, il')

In [12]:
# split the address string again
address_df = pd.DataFrame(df_CCPT1617['address'].str.split(',').tolist(), columns=['address','city','state'])

In [13]:
# check the number of unique address here
address_df['state'].unique()
print('Number of unique addresses: {}'.format(len(address_df['address'].unique())))

Number of unique addresses: 71689


In [14]:
# create a new df to save address, latitude and longitude
address_df = pd.DataFrame(address_df['address'].unique(), columns=['address'])
address_df['lat'] = np.nan
address_df['lng'] = np.nan
address_df.head()

address  lat  lng
0            500 e 46  NaN  NaN
1   6100 s archer ave  NaN  NaN
2  4200 w irving park  NaN  NaN
3        1700 w grand  NaN  NaN
4     2200 n st louis  NaN  NaN

Use geocoder here to fetch the latitude and longitude for the ticket address

In [15]:
import geocoder
import requests
import time
import datetime

In [16]:
class GeoSessions:
    def __init__(self):
        self.Komoot = requests.Session()
        self.Arcgis = requests.Session()
        self.USCensus = requests.Session()
        self.OSM = requests.Session()

def create_sessions():
    return GeoSessions()

def geocode_address(address, s):
    g = geocoder.komoot(address, session=s.Komoot)
    if (g.ok == False):        
        g = geocoder.osm(address, session=s.OSM)
    if (g.ok == False):
        g = geocoder.arcgis(address, session=s.Arcgis)
    if (g.ok == False):
        g = geocoder.uscensus(address, session=s.USCensus)
    return g

In [17]:
s = create_sessions()

In [18]:
# test with the first address
addr = address_df['address'][0] + ', Chicago, IL'
tmp = geocode_address(addr, s)
print(addr)
print('Latitude:  {}'.format(tmp.lat))
print('Longitude: {}'.format(tmp.lng))

500 e 46, Chicago, IL
Latitude:  41.8349087
Longitude: -87.61417004242811


In [19]:
# set a loop to fetch lat,long for all addresses, since this process takes a while, 
# later I will load the pre-saved file, this is just a demonstration
failed_inds = []
iter_between_saves = 100

In [20]:
missing_latlon_ind = address_df[address_df['lat'].isnull()][:201].index.tolist()

for i in missing_latlon_ind:
    try:
        if i%iter_between_saves == 0:
            print('got to index {}, saving df'.format(i))
            address_df.to_csv('Geocoded_CCPT_1617.csv', index=False)
        addr = address_df['address'][i] + ', Chicago, IL'
        tmp = geocode_address(addr, s)
        address_df.loc[i,'lat'] = tmp.lat
        address_df.loc[i,'lng'] = tmp.lng
    except Exception as e:
        failed_inds.append(i)
address_df.to_csv('Geocoded_CCPT_1617.csv', index=False)

got to index 0, saving df
got to index 100, saving df
got to index 200, saving df


In [21]:
address_df[address_df['lat'].isnull()]

address  lat  lng
201                  1 s wells  NaN  NaN
202            6900 n glenwood  NaN  NaN
203               2400 n mango  NaN  NaN
204         4500 n springfield  NaN  NaN
205                1 w 19th st  NaN  NaN
206             2100 e 69th st  NaN  NaN
207         2000 s ashland ave  NaN  NaN
208    1400 n dearborn parkway  NaN  NaN
209              6300 s racine  NaN  NaN
210                900 w huron  NaN  NaN
211           2400 w greenleaf  NaN  NaN
212             4400 s whipple  NaN  NaN
213             1600 e 87th st  NaN  NaN
214        3500 n southport av  NaN  NaN
215    800 w jackson boulevard  NaN  NaN
216             1700 w 51st st  NaN  NaN
217        3800 w lawrence ave  NaN  NaN
218              3000 s karlov  NaN  NaN
219               500 w roscoe  NaN  NaN
220            3300 n keystone  NaN  NaN
221           200 e pearson st  NaN  NaN
222             4500 s 59th st  NaN  NaN
223              900 w 18th st  NaN  NaN
224                1600 n vine  NaN  NaN
225             1700 w 18th st  NaN  NaN
226               1200 w barry  NaN  NaN
227           800 w chicago av  NaN  NaN
228         4400 n western ave  NaN  NaN
229                5200 w race  NaN  NaN
230            600 w taylor st  NaN  NaN
...                        ...  ...  ...
71659         2300 n menard av  NaN  NaN
71660         2700 n francsico  NaN  NaN
71661           1900 e 23rd st  NaN  NaN
71662           1800 w 64th st  NaN  NaN
71663              400 s avers  NaN  NaN
71664     02100 w armitage ave  NaN  NaN
71665           4000 s 31st st  NaN  NaN
71666      6700 n oliphant ave  NaN  NaN
71667             1500 w 99ths  NaN  NaN
71668      1700 s canal street  NaN  NaN
71669          2400 e randolph  NaN  NaN
71670             2 e 119th st  NaN  NaN
71671     2900 w congerss pwky  NaN  NaN
71672   10700 s sacramento ave  NaN  NaN
71673           5900 s melvina  NaN  NaN
71674       3400 n shakespeare  NaN  NaN
71675     200 w diversey parkw  NaN  NaN
71676       5300 w crystal ave  NaN  NaN
71677        900 s laramie ave  NaN  NaN
71678            6400 w seeley  NaN  NaN
71679             5200  menard  NaN  NaN
71680       800 e hyde pk blvd  NaN  NaN
71681              7 w 55th st  NaN  NaN
71682            9900 s emrald  NaN  NaN
71683           8000 s philips  NaN  NaN
71684          19000 w 47th st  NaN  NaN
71685            7500 n olcott  NaN  NaN
71686        600 s springfield  NaN  NaN
71687              1 w 112thst  NaN  NaN
71688        2000 w pensacaola  NaN  NaN

[71488 rows x 3 columns]

In [22]:
df_geoloc = pd.read_csv('./data/Geocoded_CCPT_1617.csv')
df_geoloc['address'] = df_geoloc['address'] + ', chicago, il'

In [23]:
geocoded_df = pd.merge(left=df_CCPT1617, right=df_geoloc, how='inner', on='address')
geocoded_df.head(100)

issue_date license_plate_state license_plate_type  \
0  2016-05-19 17:40:00                  IL                PAS   
1  2016-01-30 00:34:00                  IL                TMP   
2  2016-11-05 20:35:00                  IL                PAS   
3  2016-05-27 17:30:00                  IL                PAS   
4  2017-11-24 16:23:00                  IL                PAS   
5  2017-04-24 18:31:00                  IL                PAS   
6  2017-08-20 04:35:00                  IL                PAS   
7  2017-04-15 02:02:00                  IL                PAS   
8  2016-04-12 23:44:00                  IL                PAS   
9  2016-07-09 15:58:00                  IL                PAS   
10 2016-07-02 02:40:00                  IL                PAS   
11 2016-06-14 11:55:00                  IL                PAS   
12 2017-12-17 04:05:00                  IL                PAS   
13 2016-02-27 03:45:00                  IL                PAS   
14 2016-05-01 01:36:00                  IL                PAS   
15 2017-02-13 02:24:00                  IL                PAS   
16 2017-08-13 01:40:00                  IL                PAS   
17 2017-04-02 23:10:00                  IL                PAS   
18 2016-11-22 03:02:00                  IL                PAS   
19 2016-12-17 02:51:00                  IL                PAS   
20 2017-10-28 02:06:00                  IL                PAS   
21 2016-08-20 01:34:00                  IL                PAS   
22 2016-09-23 01:53:00                  IL                PAS   
23 2016-06-13 13:03:00                  IL                TXI   
24 2016-10-23 02:51:00                  IL                PAS   
25 2016-06-27 16:08:00                  IL                PAS   
26 2016-09-21 16:26:00                  IL                PAS   
27 2016-02-10 16:27:00                  IL                PAS   
28 2016-07-13 16:16:00                  IL                PAS   
29 2016-06-03 16:46:00                  IL                PAS   
..                 ...                 ...                ...   
70 2016-11-02 10:23:00                  IL                PAS   
71 2016-01-04 10:30:00                  IL                PAS   
72 2017-07-27 10:17:00                  IL                PAS   
73 2017-06-23 10:09:00                  IL                PAS   
74 2017-06-23 10:23:00                  IL                PAS   
75 2017-03-01 15:46:00                  IL                PAS   
76 2016-09-27 09:41:00                  MD                PAS   
77 2016-06-23 11:37:00                  IL                PAS   
78 2017-07-31 09:31:00                  IL                PAS   
79 2017-05-24 09:23:00                  IL                PAS   
80 2016-04-05 10:37:00                  IL                PAS   
81 2016-06-23 11:24:00                  IL                PAS   
82 2016-08-26 09:58:00                  IL                TMP   
83 2017-05-26 09:32:00                  IL                PAS   
84 2016-04-21 09:33:00                  IL                PAS   
85 2017-02-06 19:50:00                  CA                PAS   
86 2017-02-10 20:08:00                  IL                PAS   
87 2017-01-05 20:07:00                  IL                PAS   
88 2016-02-26 20:32:00                  IL                PAS   
89 2017-08-01 20:53:00                  IN                PAS   
90 2016-02-02 16:35:00                  IL                PAS   
91 2017-02-07 20:17:00                  IL                PAS   
92 2016-08-24 20:21:00                  IL                PAS   
93 2016-03-10 19:52:00                  IL                PAS   
94 2016-12-30 20:43:00                  IL                PAS   
95 2016-06-14 11:59:00                  IL                PAS   
96 2017-01-05 20:09:00                  IL                PAS   
97 2016-09-07 21:51:00                  IL                DLC   
98 2016-04-08 21:41:00                  IL                PAS   
99 2016-01-19 19:47:00                  IL     

In [24]:
import folium
import folium.plugins as plugins

In [25]:
# pick a center point for the map
chicago_lat = 41.8
chicago_lng = -87.7

In [26]:
# Find the ticket with "RESIDENTIAL PERMIT PARKING" violation, 
# check if there's any pattern in terms of the ticket issued location
df_permit = geocoded_df.loc[geocoded_df['violation_description'] == 'RESIDENTIAL PERMIT PARKING']
df_permit

issue_date license_plate_state license_plate_type  \
64     2017-11-17 18:07:00                  IL                PAS   
720    2017-12-28 00:47:00                  IL                PAS   
721    2016-02-12 00:45:00                  IL                PAS   
722    2016-08-16 20:26:00                  IL                PAS   
725    2016-10-07 17:37:00                  IL                PAS   
727    2017-09-08 18:38:00                  IL                DOM   
728    2017-10-19 17:15:00                  OH                PAS   
730    2016-08-09 17:15:00                  IL                PAS   
731    2017-07-08 19:51:00                  IL                PAS   
733    2016-08-09 17:13:00                  IL                PAS   
734    2016-04-26 17:52:00                  IL                PAS   
736    2016-09-19 17:21:00                  IL                PAS   
738    2016-05-31 19:34:00                  IL                PAS   
739    2016-06-01 17:28:00                  IL                PAS   
741    2017-09-08 17:29:00                  IL                ELE   
742    2016-06-20 17:24:00                  IL                PAS   
743    2017-10-19 17:10:00                  IL                PAS   
744    2016-08-16 19:40:00                  IL                PAS   
745    2016-09-01 20:41:00                  IL                PAS   
746    2016-08-31 19:20:00                  NJ                PAS   
747    2017-10-19 17:09:00                  IL                PAS   
749    2016-08-10 17:10:00                  CA                PAS   
750    2016-10-22 19:15:00                  IL                PAS   
753    2017-08-01 17:00:00                  IL                PAS   
754    2016-09-19 17:19:00                  IL                PAS   
758    2016-08-02 17:35:00                  AZ                PAS   
759    2017-07-08 19:49:00                  ON                PAS   
760    2016-05-05 20:42:00                  IL                PAS   
764    2016-04-11 17:25:00                  IL                PAS   
765    2016-08-10 17:19:00                  IL                PAS   
...                    ...                 ...                ...   
889067 2016-07-05 18:20:00                  IL                PAS   
889083 2017-10-10 13:16:00                  IL                TRK   
889097 2016-05-11 18:25:00                  IL                PAS   
889099 2016-04-18 21:25:00                  IL                PAS   
889103 2016-07-09 23:34:00                  IL                PAS   
889119 2017-09-05 00:37:00                  IL                PAS   
889140 2017-02-11 21:53:00                  IL                PAS   
889173 2017-05-06 08:41:00                  IL                PAS   
889184 2017-12-26 20:48:00                  IL                PAS   
889191 2017-06-18 00:32:00                  IL                PAS   
889200 2017-03-01 12:59:00                  IL                PAS   
889207 2017-04-26 00:55:00                  MI                PAS   
889220 2016-03-27 14:15:00                  IL                PAS   
889239 2017-02-11 09:28:00                  NY                PAS   
889249 2016-06-18 17:32:00                  IL                PAS   
889263 2017-03-12 01:44:00                  IL                PAS   
889276 2016-09-23 12:35:00                  IL                PAS   
889295 2017-02-26 10:10:00                  IL                PAS   
889343 2016-11-23 22:14:00                  IL                PAS   
889381 2017-04-17 02:00:00                  IL                PAS   
889474 2016-07-07 00:10:00                  IL                FFM   
889596 2017-08-30 06:17:00                  IL                PAS   
889614 2017-06-08 01:15:00                  IL                PAS   
889620 2016-05-31 17:06:00                  NJ                PAS   
889672 2016-05-19 22:41:00                  CA                PAS   
889673 2016-04-27 08:16:00                  IL                TMP   
889674 2017-05

In [27]:
# only take the latitude and longitude
df_permit_hm = df_permit[['lat','lng']]

In [28]:
# There are quite some outliers, here I will just remove the ones outside Chicago, 
# later I will do the more careful cleaning

mask_chi = ((df_permit['lat']>=41.63) & (df_permit['lat']<= 42.05) &
               (df_permit['lng']>= -88.0) & (df_permit['lng']<= -87.5))
df_permit_hm = df_permit_hm.loc[mask_chi]

In [29]:
# create an array to plot heat map of the locations
permit_data = [[row['lat'],row['lng']] for index, row in df_permit_hm.iterrows()]

In [30]:
# plot the heatmap of residential permit parking violation
m = folium.Map([chicago_lat,chicago_lng],zoom_start=10)
hm = plugins.HeatMap(permit_data,radius = 8)
hm.add_to(m)
m

Figure 2. Heatmap of residential permit parking violation
The "heatmap" for residential permit parking violation shows an interesting contrast between the northern part and the southern part of the City of Chicago, where the parking violations in the northern city have a denser concentraion compared to the south. This could reflect the population density of Chicago. I found example data for Chicago population density (e.g. https://www.arcgis.com/home/webmap/viewer.html?webmap=dfa1866898254e8c8e4eb7b70af99ed4) that supports this hypothesis. 

In addition to this plot, I also plotted the temporal change of the residential permit parking tickets issued at different time of the day. Below is a plot shows the "heatmap" for residential permit parking tickets at different hours of the day. The "north denser than south" observation still stand through different hours of the day.

While it's not surprising that not a lot tickets are issued during the night, there appear to be two peaks of tickets issuance during the day, one around 8 am, the other around 8 pm. This could be related to how the residential parking restriction is set, or other reasons such as residents returning from work around 8 pm. 

In [31]:
df_permit['Weight'] = df_permit['issue_date'].dt.hour
df_permit['Weight'] = df_permit['Weight'].astype(float)
df_permit_hmt = df_permit[['lat','lng','Weight']]

In [32]:
permit_timeseries = [[[row['lat'],row['lng']] 
                      for index, row in df_permit_hmt[df_permit_hmt['Weight'] == i].iterrows()] for i in range(0,24)]

In [33]:
hours_indx = [(datetime.time(i).strftime('%I %p')) for i in range(24)]
mt = folium.Map([chicago_lat,chicago_lng],tiles = "Stamen Toner",zoom_start=10)
hmt = plugins.HeatMapWithTime(permit_timeseries,auto_play=True,radius = 5, min_opacity = 1,index = hours_indx)
hmt.add_to(mt)
mt